# Transaction data dependency visualization
In Hyperledger-Fabric each transaction is first executed, then ordered by data dependencies, then validated against the current state of the blockchain. Because of this architecture transactions can be executed in parallel, however if a key is written to, its version  number is updated and all transactions that have not yet been validated and read the previous version number, get invalidated. They receive the validation code of MVCC_READ_CONFILCT.

If a lot of transactions receive this code, it will negatively affect performance of the system. This notebook aims to uncover the patterns that cause a lot of these conflicts, so the chaincode can be rewritten in a way that avoids this.

This notebook depends on a running explorer database. With the provided shell script, a database can be run locally, with the sample data provided in the data folder.

In [211]:
DATABASE_HOST="vm.niif.cloud.bme.hu"
DATABASE_PORT=":9702/"
# DATABASE_PORT=":5432/"
DATABASE_DATABASE="fabricexplorer"
DATABASE_USERNAME="hppoc"
DATABASE_PASSWORD="password"

import pandas as pd
import numpy as np
from sqlalchemy import create_engine
import bamboolib as bam
import matplotlib.pyplot as ptlib
import plotly.express as px
import json
import re
from datetime import datetime

# list all user defined tables and schemas
# "SELECT * FROM pg_catalog.pg_tables WHERE schemaname != 'information_schema' AND schemaname != 'pg_catalog';"

#initializing resources
engine = create_engine('postgresql://'+DATABASE_USERNAME+
                       ':'+DATABASE_PASSWORD+'@'
                       +DATABASE_HOST
                       +DATABASE_PORT
                       +DATABASE_DATABASE)

# get all transactions from database
txQuery = "SELECT * FROM transactions"
txDf = pd.read_sql(txQuery,con=engine)
# drop the ones without readsets
txDf=txDf[txDf['read_set'].isna()==False]
# drop the ones committed by lifecycle chaincode
txDf=txDf[txDf['chaincodename'].str.contains('_lifecycle')==False]
# drop the config transactions
txDf=txDf[txDf['type'].str.contains('CONFIG')==False]
# drop a bunch of unneeded coloumns
timeDf=txDf.drop(columns=["txhash","chaincode_id","endorser_msp_id","type","channel_genesis_hash","envelope_signature","creator_id_bytes", "creator_nonce", "payload_extension","tx_response","payload_proposal_hash","endorser_id_bytes","endorser_signature", "network_name","chaincode_proposal_input","read_set","write_set"])
transactions = txDf.drop(columns=["txhash","chaincode_id","endorser_msp_id","type","channel_genesis_hash","envelope_signature","creator_id_bytes", "creator_nonce", "payload_extension","tx_response","payload_proposal_hash","endorser_id_bytes","endorser_signature", "network_name","chaincode_proposal_input",])
txDf=txDf.drop(columns=["txhash","chaincode_id","endorser_msp_id","type","createdt","channel_genesis_hash","envelope_signature","creator_id_bytes", "creator_nonce", "payload_extension","tx_response","payload_proposal_hash","endorser_id_bytes","endorser_signature", "network_name"])
txDf

          id  blockid chaincodename  status     creator_msp_id  \
0          6        3          lscc   200.0  CentralBankOrgMSP   
4         10        4          cbdc   200.0  CentralBankOrgMSP   
5         11        5          cbdc   200.0           FIOrgMSP   
6         12        5          cbdc   200.0           FIOrgMSP   
7         13        5          cbdc   200.0           FIOrgMSP   
...      ...      ...           ...     ...                ...   
13603  13609      575          cbdc   200.0           FIOrgMSP   
13604  13610      575          cbdc   200.0           FIOrgMSP   
13605  13611      575          cbdc   200.0           FIOrgMSP   
13606  13612      575          cbdc   200.0           FIOrgMSP   
13607  13613      576          cbdc   200.0           FIOrgMSP   

                                                read_set  \
0      [{'chaincode': 'lscc', 'set': [{'key': 'cbdc'}]}]   
4      [{'chaincode': 'cbdc', 'set': []}, {'chaincode...   
5      [{'chaincode': 'cbdc

In [212]:
# create rows from the list of reads and writes
txDf = txDf.explode('read_set')
txDf = txDf.explode('write_set')
# drop rows with readsets containing no version number(eg no keys read) 
txDf = txDf.loc[(txDf['read_set'].astype('string').str.contains('version', case=False, regex=False, na=False))]
txDf

          id  blockid chaincodename  status     creator_msp_id  \
4         10        4          cbdc   200.0  CentralBankOrgMSP   
4         10        4          cbdc   200.0  CentralBankOrgMSP   
5         11        5          cbdc   200.0           FIOrgMSP   
5         11        5          cbdc   200.0           FIOrgMSP   
6         12        5          cbdc   200.0           FIOrgMSP   
...      ...      ...           ...     ...                ...   
13606  13612      575          cbdc   200.0           FIOrgMSP   
13607  13613      576          cbdc   200.0           FIOrgMSP   
13607  13613      576          cbdc   200.0           FIOrgMSP   
13607  13613      576          cbdc   200.0           FIOrgMSP   
13607  13613      576          cbdc   200.0           FIOrgMSP   

                                                read_set  \
4      {'chaincode': 'lscc', 'set': [{'key': 'cbdc', ...   
4      {'chaincode': 'lscc', 'set': [{'key': 'cbdc', ...   
5      {'chaincode': 'lscc'

In [213]:
# extract chaincode names to new columns from the rw-sets
txDf['r_chaincode'] =txDf['read_set'].apply(lambda x: x['chaincode'])
txDf['rs'] =txDf['read_set'].apply(lambda x: x['set'])
txDf = txDf.drop(columns=['chaincodename','read_set'])
txDf['w_chaincode'] =txDf['write_set'].apply(lambda x: x['chaincode'])
txDf['ws'] =txDf['write_set'].apply(lambda x: x['set'])
txDf = txDf.drop(columns=['write_set'])
txDf

          id  blockid  status     creator_msp_id validation_code  \
4         10        4   200.0  CentralBankOrgMSP           VALID   
4         10        4   200.0  CentralBankOrgMSP           VALID   
5         11        5   200.0           FIOrgMSP           VALID   
5         11        5   200.0           FIOrgMSP           VALID   
6         12        5   200.0           FIOrgMSP           VALID   
...      ...      ...     ...                ...             ...   
13606  13612      575   200.0           FIOrgMSP           VALID   
13607  13613      576   200.0           FIOrgMSP           VALID   
13607  13613      576   200.0           FIOrgMSP           VALID   
13607  13613      576   200.0           FIOrgMSP           VALID   
13607  13613      576   200.0           FIOrgMSP           VALID   

                                chaincode_proposal_input r_chaincode  \
4      7365740690746906741000776106365,46490726705350...        lscc   
4      7365740690746906741000776106365,

In [214]:
# create new rows from readsets, and make a separate df for reads
txDfr = txDf.drop(columns=['w_chaincode','ws']).explode('rs')
txDfr = txDfr.rename(columns={'r_chaincode': 'chaincode','rs':'key'})
# add an access type column to reads
txDfr['access_type'] = txDfr['key'].apply(lambda x: 'READ')
# add version coloums to the reads (extract the version info from the json)
txDfr['version_block'] = txDfr['key'].apply(lambda x: np.nan if str(x) == 'nan' else x['version']['block_num']['low'])
txDfr['version_tx'] = txDfr['key'].apply(lambda x: np.nan if str(x) == 'nan' else x['version']['tx_num']['low'])
# create new rows fro writesets, and make a separate df for writes
txDfw = txDf.drop(columns=['r_chaincode','rs']).explode('ws')
txDfw = txDfw.rename(columns={'w_chaincode': 'chaincode','ws':'key'})
# add an access type column to writes, and classify them as writes or deletes
conditions = [
    txDfw['key'].str =='nan',
    txDfw['key'].str.contains("'is_delete': True",na=False)
]
choices = [np.nan,'DELETE']
txDfw['access_type'] = np.select(conditions,choices,default='WRITE')

# append the df with the writes to the df with the reads
txDf = txDfr.append(txDfw).reset_index(drop=True).rename(columns={'id':'txid'})
# extract the keys from the jsons from the rwsets
txDf['key']=txDf['key'].apply(lambda x:np.nan if str(x) == 'nan' else x['key'])
# drop the ones with no keys
txDf = txDf.dropna(subset=['key'])
# drop rows with keys that were read by lifecycle chaincodes
txDf = txDf.loc[~(txDf['chaincode'].isin(['lscc','_lifecycle']))]
# drop the duplicates created by creating new rows from the rwsets
txDf = txDf.drop_duplicates(keep='first')
# replace delimiting null characters in compoiste keys
txDf['key'] = txDf['key'].str.replace('\x00','')
txDf

         txid  blockid  status creator_msp_id validation_code  \
7576     3798      136   200.0       FIOrgMSP           VALID   
7608     3813      136   200.0       FIOrgMSP           VALID   
7624     3820      136   200.0       FIOrgMSP           VALID   
7628     3821      136   200.0       FIOrgMSP           VALID   
7664     3838      136   200.0       FIOrgMSP           VALID   
...       ...      ...     ...            ...             ...   
122707  13611      575   200.0       FIOrgMSP           VALID   
122712  13612      575   200.0       FIOrgMSP           VALID   
122713  13612      575   200.0       FIOrgMSP           VALID   
122718  13613      576   200.0       FIOrgMSP           VALID   
122719  13613      576   200.0       FIOrgMSP           VALID   

                                 chaincode_proposal_input chaincode  \
7576    069074550697473,307866356639613031386532353461...      cbdc   
7608    069074550697473,307830396335613663633461353735...      cbdc   
7624  

## Keys and the number of reads on each of them
Seeing a lot of reads on a key might not be concerning, because if it is not written often, it likely won't cause a lot of MVCCs.

In [215]:
# df containing reads only
txDfr=txDf[txDf['access_type']=='READ']
labels={"x":"Read keys","y":"Number of reads"}
# group by keys and count the occurrences
reads= txDfr.groupby(['key']).size()
reads = pd.DataFrame(reads)
reads.columns = [str(column) for column in reads.columns]
reads = reads.reset_index()
# sort keys by read amounts descending
reads = reads.sort_values(by=['0'], ascending=[False])
# plot the first 10 keys
fig = px.bar(reads.head(10), x='key', y='0', labels={'0':'reads'})
fig

## Keys and the number of writes on each of them
Seeing a lot of writes on a key might not be concerning, because if it is not read often, it likely won't cause  a lot of MVCCs.

In [216]:
# df containing writes only
txDfw=txDf[txDf['access_type']=='WRITE']
labels={"x":"Written keys","y":"Number of writes"}
# group by keys and count the occurrences
writes = txDfw.groupby(['key']).size()
writes = pd.DataFrame(writes)
writes.columns = [str(column) for column in writes.columns]
writes = writes.reset_index()
# sort keys by write amounts descending
writes = writes.sort_values(by=['0'], ascending=[False])
# plot the first 10 keys
fig = px.bar(writes.head(10), x='key', y='0', labels={'0':'writes'})
fig

## Cumulative sum of valid txs - mvcc txs
If all goes well, this graph only shows a monotonically increasing line. However, it is great to visualize waves of mvcc conflicts, which will be visible as the slope of the graph will decrease, or even turn negative.

In [217]:
# df containing transactions sorted by tx ids
transactions = transactions.sort_values(by=['id'], ascending=[True])
# function to assign -1 to mvccs, +1 to valid, 0 to all else
def gradeValidation(code):
    if code=='MVCC_READ_CONFLICT':
        return -1
    elif code=='VALID':
        return +1
    else:
        return 0
# function to find keys in the rwsets' jsons
def findKeys(string):
    pat = r"(?<='key': ').+?(?=')"
    return re.findall(pat,string)
# add new column to df and assign values to transactions based on validation code
transactions['delta']= transactions['validation_code'].apply(lambda x: gradeValidation(x))
# extract keys from rwsets' jsons
transactions['read_keys'] = transactions['read_set'].apply(lambda x: findKeys(str(x)))
transactions['written_keys'] = transactions['write_set'].apply(lambda x: findKeys(str(x)))
# calculate the cumulative sum of the values assigned based on validation codes
transactions['delta_cumsum'] = transactions['delta'].cumsum()
transactions
# plot the data
fig = px.line(transactions.sort_values(by=['id'], ascending=[True]), x='id', y='delta_cumsum', hover_data=['read_keys', 'written_keys'])
fig.update_xaxes(title_text='transaction id')
fig.update_yaxes(title_text='cumsum(valid-mvcc)')
fig

## Transactions grouped by validation codes
This graph just shows the number of transactions in each of the validation code groups.

In [218]:
labels={"x":"Validation code","y":"Qty"}
# group transactions by validation codes, and calculate the size of each group
codes=transactions.groupby(['validation_code']).size().reset_index().rename(columns={0:'size'})
# sort rows by group size
codes = codes.sort_values(by=['size'], ascending=[False])
# plot the data
fig = px.bar(x=codes['validation_code'], y=codes['size'],labels=labels)
fig

If your dataset contains large amounts of mvcc conflicts, please uncomment the cell below, and process the exported csv in the mvcc-finder notebook, that runs the kotlin kernel.

In [219]:
# # sort by txid and access type ascending
# df = txDf.sort_values(by=['txid', 'access_type'], ascending=[True, True])
# # add new column for counting mvccs caused by each keyaccess
# df['mvcc_cause']=0
# # write df to disk as csv for processing with kotlin notebook
# df.to_csv('data/postfault0.csv')

After processing it with the kotlin notebook, please uncomment the cell below, to see a plot of the results.

## Keys and the amount of MVCCs they caused
A key causes an mvcc conflict if it is read with a version number, that is different from the one in the current state of the blockchain.

In [220]:
# # read the csv containing the processed data
# df = pd.read_csv("data/postfault0_mvccs.csv")
# # plot the first 10 keys
# fig = px.bar(df.head(10), x='key', y='mvccs_caused')
# fig

**If you processed the dataframe with the kotlin notebook please dont run the next 2 cells.**

In [221]:
# lib for faster apply
import swifter
# sort by txid and access type ascending, drop old index
df = txDf.sort_values(by=['txid', 'access_type'], ascending=[True, True]).reset_index().drop(columns=['index'])
# add new column for counting mvccs caused by each keyaccess
df['mvcc_cause']=0
# function to find the mvcc causing keyaccess
def findCause(df,blockId,key,version,access,validation,mvcc):
    # if the access type is read and validation code is mvcc
    if validation=='MVCC_READ_CONFLICT' and access=='READ':
        # find all valid writes for the given key, in the interval between the keyaccess
        # and the block specified in the keyaccess' version
        subset = df[((df['blockid']<=blockId)&(df['blockid']>version)&(df['key']==key)&(df['access_type']=='WRITE')&(df['validation_code']=='VALID'))]
        # if the subset isn't empty
        if(len(subset)>0):
            # found the last valid write, +1 mvccs caused by it
            df['mvcc_cause'].iloc[[subset.tail(1).index[0]]]=df['mvcc_cause'].iloc[[subset.tail(1).index[0]]]+1

#apply the function to every row of the df
df.swifter.apply(lambda x: findCause(df,x['blockid'],x['key'],x['version_block'],x['access_type'],x['validation_code'],x['mvcc_cause']),axis=1)
df

Pandas Apply:   0%|          | 0/40907 [00:00<?, ?it/s]

        txid  blockid  status     creator_msp_id validation_code  \
0         10        4   200.0  CentralBankOrgMSP           VALID   
1         11        5   200.0           FIOrgMSP           VALID   
2         11        5   200.0           FIOrgMSP           VALID   
3         12        5   200.0           FIOrgMSP           VALID   
4         12        5   200.0           FIOrgMSP           VALID   
...      ...      ...     ...                ...             ...   
40902  13612      575   200.0           FIOrgMSP           VALID   
40903  13613      576   200.0           FIOrgMSP           VALID   
40904  13613      576   200.0           FIOrgMSP           VALID   
40905  13613      576   200.0           FIOrgMSP           VALID   
40906  13613      576   200.0           FIOrgMSP           VALID   

                                chaincode_proposal_input chaincode  \
0      7365740690746906741000776106365,46490726705350...      cbdc   
1      63726561746541646472657373,307861353

## Keys and the amount of MVCCs they caused
A key causes an mvcc conflict if it is read with a version number, that is different from the one in the current state of the blockchain.

In [222]:
# group by keys and calculate the sum of mvccs they caused
df = df.groupby(['key']).agg(mvccs_caused=('mvcc_cause', 'sum')).reset_index()
# Keep rows where mvccs_caused > 0
df = df.loc[df['mvccs_caused'] > 0]
# sort rows by mvccs caused descending
df = df.sort_values(by=['mvccs_caused'], ascending=[False])
# plot the first 10 keys
fig = px.bar(df.head(10), x='key', y='mvccs_caused')
fig

In [223]:
# copy the df with reads only
distDf = txDfr.copy()
# add a write distance column based on key version(block only) and current blockid
distDf['last_write_dist']=distDf['blockid']-distDf['version_block']
distDf

        txid  blockid  status creator_msp_id validation_code  \
7576    3798      136   200.0       FIOrgMSP           VALID   
7608    3813      136   200.0       FIOrgMSP           VALID   
7624    3820      136   200.0       FIOrgMSP           VALID   
7628    3821      136   200.0       FIOrgMSP           VALID   
7664    3838      136   200.0       FIOrgMSP           VALID   
...      ...      ...     ...            ...             ...   
54595  13611      575   200.0       FIOrgMSP           VALID   
54600  13612      575   200.0       FIOrgMSP           VALID   
54601  13612      575   200.0       FIOrgMSP           VALID   
54606  13613      576   200.0       FIOrgMSP           VALID   
54607  13613      576   200.0       FIOrgMSP           VALID   

                                chaincode_proposal_input chaincode  \
7576   069074550697473,307866356639613031386532353461...      cbdc   
7608   069074550697473,307830396335613663633461353735...      cbdc   
7624   06907455069747

## Average distance to last write of a key
If the block version number of the read is subtracted from the blockid of the transaction, we get the distance to the last write performed on the key. If this is averaged over all reads of the key, we get a kind of "hotness" indicator. The less "hot" the key is, the less likely it is to cause an MVCC.

In [224]:
# group by keys and calculate the average distance to last write
dist = distDf.groupby(['key']).agg(last_write_dist_mean=('last_write_dist', 'mean')).reset_index()
# sort rows by average distance to last write ascending
dist = dist.sort_values(by=['last_write_dist_mean'], ascending=[True])
# plot the first 10 keys
fig = px.bar(dist.head(10), x='key', y='last_write_dist_mean')
fig

## Transactions/second

In [249]:
# df with transactions and their creation dates
tps = timeDf.drop(columns=["chaincodename","status","creator_msp_id",])
# sort rows by creation date ascending
tps = tps.sort_values(by=['createdt'], ascending=[True])
# reduce creation time resolution to seconds
tps['createdt'] = pd.to_datetime(tps['createdt'].dt.strftime('%Y-%m-%d %H:%M:%S'),format='%Y-%m-%d %H:%M:%S')
# calculate transactions created/second
tps = tps.groupby(['createdt']).size()
# plot the data
px.line(x=tps.index,y=tps.values,labels={'x':'Time','y':'Tps'})

General data about the transactions per second. "Count" here means the duration of the test, in seconds. 

In [250]:
tps.describe()

count    184.000000
mean      73.940217
std       25.943859
min        1.000000
25%       60.750000
50%       74.500000
75%       89.250000
max      144.000000
dtype: float64

# Transactions/second by validation code
The same data, but transaction count/second is colored by validation code. It helps visualize the amounts relative to eachother.

In [251]:
# df with transactions and their creation dates
tps = timeDf.drop(columns=["chaincodename","status","creator_msp_id",])
# reduce creation time resolution to seconds
tps['createdt'] = pd.to_datetime(tps['createdt'].dt.strftime('%Y-%m-%d %H:%M:%S'),format='%Y-%m-%d %H:%M:%S')
# group by createdt and validation code
tps = tps.groupby(by=['createdt','validation_code'],as_index=False).size()
# Pivot df from long to wide format using the variable column 'validation_code' and the value column 'size'
tps = tps.pivot(index='createdt', columns='validation_code', values='size').reset_index()
# fill nan values with zeros
tps = tps.fillna(0)
# melt back to original shape
tps = tps.melt(id_vars=['createdt'],var_name='validation_code')
# sort rows by createdt ascending (A-Z)
tps = tps.sort_values(by=['createdt'], ascending=[True])
# plot the data
fig = px.area(tps, x='createdt', y='value', color='validation_code', color_discrete_sequence=px.colors.qualitative.G10[::-1])
fig.update_xaxes(title_text='Time')
fig.update_yaxes(title_text='Tx/sec')
fig

## Number MVCCs/second
This graph shows how many transactions are validated with the code MVCC_READ_CONFLICT each second. 

In [228]:
# df with transactions and their creation dates
mvccps = timeDf.drop(columns=["chaincodename","status","creator_msp_id",])
# sort rows by creation date ascending
mvccps = mvccps.sort_values(by=['createdt'], ascending=[True])
# reduce creation time resolution to seconds
mvccps['createdt'] = pd.to_datetime(mvccps['createdt'].dt.strftime('%Y-%m-%d %H:%M:%S'),format='%Y-%m-%d %H:%M:%S')
# keep transactions with validation code MVCC_READ_CONFLICT
mvccps = mvccps.loc[mvccps['validation_code'].isin(['MVCC_READ_CONFLICT'])]
# calculate number of mvcc transactions created/second
mvccps = mvccps.groupby(['createdt']).size()
# plot the data
px.line(x=mvccps.index,y=mvccps.values,labels={'x':'Time','y':'MVCCS/sec'})

## Read keys and the number of valid and mvcc transactions they occurred in
A key that was read as part of a transaction marked with mvcc might not be the cause of the mvcc, but can reveal patterns in the data.

In [229]:
# group reads by keys and validation code, and calculate the size of each group
keycodedf = txDfr.groupby(by=['key','validation_code'],as_index=False).size()
# Pivot dataframe from long to wide format using the variable column 'validation_code' and the value column 'size'
# this is done so the data can be sorted by mvccs descending
keycodedf = keycodedf.pivot(index='key', columns='validation_code', values='size').reset_index()
# drop endorsement policy failure column
if 'ENDORSEMENT_POLICY_FAILURE' in keycodedf.columns:
    keycodedf = keycodedf.drop(columns=['ENDORSEMENT_POLICY_FAILURE'])
# sort by MVCC_READ_CONFLICT descending, keep the first 10
keycodedf = keycodedf.sort_values(by=['MVCC_READ_CONFLICT'], ascending=[False]).head(10)
# return to original shape so it can be plotted
keycodedf = keycodedf.melt(id_vars=['key'],var_name='validation_code')
# fill nans with 0, as they were before transformations
keycodedf = keycodedf.fillna(0)
# plot the data
labels={"key":"Key","value":"Occurrence in transactions"}
fig = px.bar(keycodedf, x='key', y='value', color='validation_code', barmode='group',labels=labels)
fig

## Keys and the ratio of valid/mvcc reads done on them.
If a key has a high ratio, it might be troublesome. It might not have caused the mvcc, but it might reveal patterns in the data.

In [230]:
# previously created df with keys and their number of occurrences in each validation code group
# drop the endorsement policy failure group
ratio = txDfr.groupby(['key','validation_code']).size().reset_index().rename(columns={0:'size'})
ratio = ratio.loc[~(ratio['validation_code'].isin(['ENDORSEMENT_POLICY_FAILURE']))]
# pivot the table on validation codes
ratio = ratio.pivot_table(index=['key'], 
            columns=['validation_code'], values='size').fillna(0)
# calculate the ratio of the number of occurrences of each key in mvcc transactions/valid transactions
ratio['ratio']=ratio['MVCC_READ_CONFLICT']/ratio['VALID']
# drop rows where ratio is >= infinity  or <= 0
ratio = ratio.loc[(~(ratio['ratio'] >= np.inf) | (ratio['ratio'] <= 0))]
# sort by the ratio descending
ratio = ratio.reset_index()
ratio = ratio.sort_values(by=['ratio'], ascending=[False])
# plot the first 10
fig = px.bar(ratio.head(10), x='key', y='ratio',title='Ratio of MVCC/Valid')
fig

## Number of read keyaccesses done by each chaincode
This graph visualizes which chaincodes are the most actively reading keys.

In [231]:
# group key reads by chaincodes and plot the size of each group 
labels={"x":"Chaincode","y":"Key reads"}
fig = px.bar(x=txDfr['chaincode'].unique(),y=txDfr['chaincode'].value_counts(),labels=labels)
fig

## Number of write keyaccesses done by each chaincode
This graph visualizes which chaincodes are the most actively writing keys.

In [232]:
# group key writes by chaincodes and plot the size of each group 
labels={"x":"Chaincode","y":"Key writes"}
fig = px.bar(x=txDfw['chaincode'].unique(),y=txDfw['chaincode'].value_counts(),labels=labels)
fig

In [233]:
# all user defined tables in the explorer db
query = "SELECT * FROM pg_catalog.pg_tables WHERE schemaname != 'information_schema' AND schemaname != 'pg_catalog';"
idkdf = pd.read_sql(query,con=engine)
idkdf

  schemaname           tablename tableowner tablespace  hasindexes  hasrules  \
0     public              blocks      hppoc       None        True     False   
1     public          chaincodes      hppoc       None        True     False   
2     public  peer_ref_chaincode      hppoc       None        True     False   
3     public             channel      hppoc       None        True     False   
4     public                peer      hppoc       None        True     False   
5     public    peer_ref_channel      hppoc       None        True     False   
6     public             orderer      hppoc       None        True     False   
7     public        transactions      hppoc       None        True     False   
8     public               users      hppoc       None        True     False   
9     public          write_lock      hppoc       None        True     False   

   hastriggers  rowsecurity  
0        False        False  
1        False        False  
2        False        False  